In [5]:
import math

# Set sun, earth position
sun_mass = 1.98892 * 10**30
earth_mass = 5.9742 * 10**24
sun_to_earth = 1 # AU, check to make sure gravity is in AU

# Functions for computing gravity vectors
Gsc = 1.361 # kW/m2
A = 1 # m**2     # sail area
C_SRP    = 2.00 # SRP coefficent, C_SRP = 1 for perfectly absorbing, C_SRP = 2 for perfectly reflective  solar sail
# FN= 2GsccAcos2(α)≈(9μN/m2) cos2(α)

dim = 2 # 2 or 3d sim, starting with 2

# The gravitational constant G
G = 6.67428e-11

# Assumed scale: 100 pixels = 1AU.
AU = (149.6e6 * 1000)     # 149.6 million km, in meters.
SCALE = 250 / AU

# constants for inertial properties and torques
global r_ss, rp_ss, A_ss, Ap_ss, hp_ss, lp_ss, P_ss
r_ss = 0.56 #m, 
rp_ss = 0.565 #m
A_ss = 1 #m**2, 
Ap_ss = 0.02 #m**2
hp_ss = 10E-2 #m  
lp_ss = 20E-2 #m.
m_mp = 0.001 # kg (1gram)
m_ss = 0.0016 # kg (1.6grams)
mp_ss = 0.000032 # kg (32mg) 
P_ss = 9E-6 # uPa. (estimate)

# equations for roll flag control
# thetap_r = 2*math.asin(dyp_r/2/lp_ss)
# alphap_r = alpha - thetap_r

# Fp_s = f(alpha_roll, theta) = P_ss*Ap_ss*cos(alphap_r)**3
def Fp_s(alpha_r):
    return P_ss*Ap_ss*(math.cos(alpha_r)**2)

# F_s = f(alpha)  = P_ss*A_ss* cos(alpha)**3
def F_s(alpha_r):
    return P_ss*A_ss*(math.cos(alpha_r)**2)

# dx,dz in 0-10mm
#def T_yy(angle):
    # T_yy = Fp_s * rp_ss * math.sin(thetap_r) # = I_yy*theta_dot_dot

def T_zz(angle, dx):
    # T_zz = F_s*dx #  I_zz*alpha_dot_dot
    return F_s(angle)*dx

def T_xx(angle, dz):
    # T_xx = F_s*dz #  I_xx*alpha_dot_dot
    return F_s(angle)*dz

def inertials(dx,dy,dz,m_mp = 0.001, m_ss = 0.0016):
    ratio = m_mp/(m_ss+m_mp)
    x_ss = dx*ratio
    x_mp = dx*(1-ratio)
#     y_ss = dy*ratio
    y_tot = 2 #.05 # 2
    y_ss = y_tot*ratio
#     y_mp = dy*(1-ratio)
    y_mp = y_tot*(1-ratio)
    z_ss = dz*ratio
    z_mp = dz*(1-ratio)

    I_yy = 1 / 2 * m_ss * r_ss **2+ m_ss * (x_ss **2+ z_ss **2)+mp_ss * rp_ss **2+1 / 12 * mp_ss * hp_ss **2 + m_mp * (x_mp **2+z_mp**2)
    I_zz = 1 / 4 * m_ss * r_ss **2+m_ss * (x_ss **2+ y_ss **2)+m_mp * (x_mp**2+y_mp **2)
    I_xx = 1 / 4 * m_ss * r_ss **2+m_ss * (z_ss **2+ y_ss **2)+m_mp * (z_mp**2+y_mp **2)
    return I_xx, I_yy, I_zz

f = F_s(0)
n = 100
alpha = np.linspace(-np.pi/2,np.pi/2,n)
dx = np.linspace(-0.01,0.01,n)
dz = np.linspace(-0.01,0.01,n)
xx,zz = np.meshgrid(dx,dz)
rates = np.zeros((n,n,3))
for i, x in enumerate(dx):
    for j, a in enumerate(alpha):
        f = F_s(a)
        z = 0
        ix, iy, iz = inertials(x,0,z)
        tx = f *x #z
        ty = 0
        tz = f* z #x
        ox = tx/ix
        oy = 0
        oz = tz/iz
        rates[i,j,0] = ox
        rates[i,j,2] = oz 

        
import plotly.graph_objects as go

fig = go.Figure(data=go.Heatmap(
        z=rates[:,:,0],
        x=alpha,
        y=dx,
        colorscale='Viridis')
                )

fig.update_layout(
    title='Angular Rates vs Sun Angle vs Input',
    xaxis_title='cone angle (rad)',
    yaxis_title='input motion (m)')

fig.show()

In [6]:
import numpy as np

# PID controller for roll (add noise to simulation)
class PID():
    def __init__(self, desired,
                 kp, ki, kd,
                 ilimit, dt, outlimit=np.inf,
                 samplingRate=0, cutoffFreq=-1,
                 enableDFilter=False):

        # internal variables
        self.error = 0
        self.error_prev = 0
        self.integral = 0
        self.deriv = 0
        self.out = 0

        # constants
        self.desired = desired
        self.kp = kp
        self.ki = ki
        self.kd = kd

        # limits integral growth
        self.ilimit = ilimit

        # limits ridiculous actions. Should set to variance
        self.outlimit = outlimit

        # timee steps for changing step size of PID response
        self.dt = dt
        self.samplingRate = samplingRate  # sample rate is for filtering

        self.cutoffFreq = cutoffFreq
        self.enableDFilter = enableDFilter

        if cutoffFreq != -1 or enableDFilter:
            raise NotImplementedError('Have not implemnted filtering yet')

    def reset(self):
        # internal variables
        self.error = 0
        self.error_prev = 0
        self.integral = 0
        self.deriv = 0

    def update(self, measured):

        # init
        self.out = 0.

        # update error
        self.error_prev = self.error

        # calc new error
        self.error = self.desired - measured

        # proportional gain is easy
        self.out += self.kp * self.error

        # calculate deriv term
        self.deriv = (self.error - self.error_prev) / self.dt

        # filtter if needed (DT function_)
        if self.enableDFilter:
            print('Do Filter')
            self.deriv = self.deriv

        # calcualte error value added
        self.out += self.deriv * self.kd

        # accumualte normalized eerror
        self.integral = self.error * self.dt

        # limitt the integral term
        if self.ilimit != 0:
            self.integral = np.clip(self.integral, -self.ilimit, self.ilimit)

        self.out += self.ki * self.integral

        # limitt the total output
        if self.outlimit != 0:
            self.out = np.clip(self.out, -self.outlimit, self.outlimit)

        return self.out

In [7]:

# need info about initial condition of orbit

# v = np.sqrt(mu/r)

# low orbit: 180-20000 km
# mid orbit: 2000-35780 km
# high orbit: >35,780 km

# https://en.wikipedia.org/wiki/Orbital_speed

# some targets in solar sail angle at different places in orbit
# XY Plane / polar works. 
# 
targets_visual =  np.array([[90, -90], 
            [135, -67.5], 
            [180, -45],
            [225, -22.5],
            [270, 0],
            [315, 22.5],
            [0, 45], 
            [45, 67.5], 
            [89.9, 90]])

targets_actual = targets_visual - np.array([90,0])
print(targets_actual)
            
          
print([(angle-90)/2 - 90 for angle in [90, 180, 270, 360, 450]])          

[[ 0.00e+00 -9.00e+01]
 [ 4.50e+01 -6.75e+01]
 [ 9.00e+01 -4.50e+01]
 [ 1.35e+02 -2.25e+01]
 [ 1.80e+02  0.00e+00]
 [ 2.25e+02  2.25e+01]
 [-9.00e+01  4.50e+01]
 [-4.50e+01  6.75e+01]
 [-1.00e-01  9.00e+01]]
[-90.0, -45.0, 0.0, 45.0, 90.0]


In [11]:
import math

mu = 3.986004418*10**14 # SGP earth


def grav(x,y, mass1, mass2):
    d = np.sqrt(x**2+y**2)
    f = G * mass1 * mass2 / (d**2)

    # Compute the direction of the force.
    theta = math.atan2(y, x)
    fx = math.cos(theta) * f
    fy = math.sin(theta) * f
    return -fx, -fy
    
def earth2clock(angle):
    # convert from earth position to desired clock angle.
    # to start with, will just use this as the actual angle
    angle = np.rad2deg(angle)
    while angle < 90:
        angle += 360
    return (angle-90)/2 - 90
    
def clock2force(angle):
    # for now assumes the y distance from the sun line is 0
    force_mag = P_ss*Ap_ss*(math.cos(angle)**2)
    return force_mag*math.cos(angle), force_mag*math.sin(angle)
    
    
    # visualize
# from https://medium.com/analytics-vidhya/simulating-the-solar-system-with-under-100-lines-of-python-code-5c53b3039fc6
import plotly
import plotly.graph_objects as go

# ORBIT SIM, LONG
init_orbit = 30000E3
# 1.496e+11 m in 1 AU
e = np.array([0,0])
# r = np.array([0, -6.684587e-5])*1.496e+11 # xy pos sail relative to earth, 10000km below in this diagram
r = np.array([0, -init_orbit]) # xy pos sail relative to earth, 10000km below in this diagram
s = np.array([-1, 0])*1.496e+11 # sun is 1 AU to the "left" of earth

mu = 3.986004418*10**14 # SGP earth

m_ss = 0.001
m_earth =  5.972 * 10**24 

n_steps = 10000
t_vec = np.linspace(0,100000, n_steps)
v0 = np.sqrt(np.abs(mu/r[1]))
v0_sail = np.array([v0,0])
clock0 = 0



x,y = r
v = v0_sail
dt = 60 # seconds

# arrays to store and plot
Xs = []
Ys = []
F_sail = []
F_grav = []
Vs = []

for t in range(n_steps): #t_vec:
    print(f"===== Time {t*dt}(s) =====")
    sun2sail = r + np.array([x,y])
    earth_angle = math.atan2(y, x)
    clock_angle = earth2clock(earth_angle) # current hard code "control"

    f_ss = np.array(clock2force(np.deg2rad(clock_angle)))
    f_ge = np.array(grav(x,y,m_ss,m_earth))
    f_gs = np.array([0,0 ]) # no sun gravity yet
    F_sail.append(f_ss)
    F_grav.append(F_grav)
                  
    x = x + v[0]*dt
    y = y + v[1]*dt
    Xs.append(x)
    Ys.append(y)
    f_tot = f_ss + f_ge + f_gs
    
                  
    v = v + (f_tot/m_ss)*dt
    Vs.append(v)
                  
    print(f"- Angle from earth to sail about orbit circle {earth_angle}")
    print(f"- Earth angle {np.rad2deg(earth_angle)}")
    print(f"- Clock angle {clock_angle}")
    print(f"- XY force sail {f_ss}")
    print(f"- XY force grav {f_ge}")
    print(f"- XY pos [{x/1000},{y/1000}] km")
    print(f"- Velocity at this step {v}")
    print(f"- Radius {np.sqrt(x**2+y**2)/1000} km")
    print()

===== Time 0(s) =====
- Angle from earth to sail about orbit circle -1.5707963267948966
- Earth angle -90.0
- Clock angle 0.0
- XY force sail [1.8e-07 0.0e+00]
- XY force grav [-2.71183067e-20  4.42875557e-04]
- XY pos [218.70540234754148,-30000.0] km
- Velocity at this step [3645.10083913   26.57253344]
- Radius 30000.797190291727 km

===== Time 60(s) =====
- Angle from earth to sail about orbit circle -1.5635062758622604
- Earth angle -89.58231084912454
- Clock angle 0.20884457543772328
- XY force sail [1.79996413e-07 6.56094414e-10]
- XY force grav [-3.22838519e-06  4.42840254e-04]
- XY pos [437.4114526950829,-29998.4056479936] km
- Velocity at this step [3644.9179358    53.14298802]
- Radius 30001.59446097029 km

===== Time 120(s) =====
- Angle from earth to sail about orbit circle -1.5562162033572495
- Earth angle -89.16462046224305
- Clock angle 0.41768976887846065
- XY force sail [1.79985651e-07 1.31212975e-09]
- XY force grav [-6.45626522e-06  4.42781417e-04]
- XY pos [656.1065

- Earth angle -28.658662766203143
- Clock angle 30.67066861689844
- XY force sail [1.14535424e-07 6.79268772e-08]
- XY force grav [-0.00038387  0.0002098 ]
- XY pos [26593.47281218857,-14284.840363652569] km
- Velocity at this step [1748.15123717 3206.78224379]
- Radius 30187.24002666773 km

===== Time 8880(s) =====
- Angle from earth to sail about orbit circle -0.4929286346601342
- Earth angle -28.24273036717176
- Clock angle 30.87863481641412
- XY force sail [1.13795102e-07 6.80473439e-08]
- XY force grav [-0.00038533  0.00020698]
- XY pos [26698.36188641902,-14092.433429025456] km
- Velocity at this step [1725.03846557 3219.2051554 ]
- Radius 30189.388986359198 km

===== Time 8940(s) =====
- Angle from earth to sail about orbit circle -0.48566988216044
- Earth angle -27.826834484409243
- Clock angle 31.086582757795384
- XY force sail [1.13053563e-07 6.81621664e-08]
- XY force grav [-0.00038676  0.00020415]
- XY pos [26801.864194353475,-13899.28111970147] km
- Velocity at this step [

- Velocity at this step [-1311.25278452  3384.2829753 ]
- Radius 30575.890520126835 km

===== Time 16200(s) =====
- Angle from earth to sail about orbit circle 0.3854798160261996
- Earth angle 22.086366545780667
- Clock angle 56.04318327289033
- XY force sail [3.13689833e-08 4.65821233e-08]
- XY force grav [-0.00039506 -0.00016031]
- XY pos [28253.499228938697,11699.70758175276] km
- Velocity at this step [-1334.95470565  3374.66722347]
- Radius 30580.11406417842 km

===== Time 16260(s) =====
- Angle from earth to sail about orbit circle 0.3926001386370741
- Earth angle 22.49433098015535
- Clock angle 56.24716549007766
- XY force sail [3.08735003e-08 4.62005104e-08]
- XY force grav [-0.0003938  -0.00016307]
- XY pos [28173.40194659954,11902.187615161049] km
- Velocity at this step [-1358.58104094  3364.88561855]
- Radius 30584.352981077624 km

===== Time 16320(s) =====
- Angle from earth to sail about orbit circle 0.3997188520636799
- Earth angle 22.902203215062976
- Clock angle 56.451

- Clock angle 84.08611571983252
- XY force sail [1.96883278e-10 1.90069536e-09]
- XY force grav [-8.3511455e-05 -3.9878118e-04]
- XY pos [6202.212238912809,30662.172591969087] km
- Velocity at this step [-3484.84468179   785.46100963]
- Radius 31283.16263928921 km

===== Time 24660(s) =====
- Angle from earth to sail about orbit circle 1.3712135603739317
- Earth angle 78.5647498205334
- Clock angle 84.2823749102667
- XY force sail [1.77987086e-10 1.77766727e-09]
- XY force grav [-8.07493225e-05 -3.99204279e-04]
- XY pos [5993.121558005581,30709.300252546913] km
- Velocity at this step [-3489.68963046   761.50885956]
- Radius 31288.63416658051 km

===== Time 24720(s) =====
- Angle from earth to sail about orbit circle 1.3780622238467761
- Earth angle 78.95714933283278
- Clock angle 84.47857466641639
- XY force sail [1.60339687e-10 1.65868977e-09]
- XY force grav [-7.79861519e-05 -3.99608140e-04]
- XY pos [5783.74018017804,30754.990784120688] km
- Velocity at this step [-3494.36878996   

- XY force grav [ 0.00027302 -0.00027627]
- XY pos [-22669.934985159518,22639.647552516915] km
- Velocity at this step [-2524.72752118 -2439.82384181]
- Radius 32038.720223091692 km

===== Time 33480(s) =====
- Angle from earth to sail about orbit circle 2.356862945438126
- Earth angle 135.03829966437664
- Clock angle -67.48085016781168
- XY force sail [ 1.01121216e-08 -2.43897613e-08]
- XY force grav [ 0.00027476 -0.00027439]
- XY pos [-22821.418636430182,22493.258122008338] km
- Velocity at this step [-2508.24148495 -2456.28870987]
- Radius 32043.155423935652 km

===== Time 33540(s) =====
- Angle from earth to sail about orbit circle 2.3634361787887497
- Earth angle 135.41491819312202
- Clock angle -67.29254090343899
- XY force sail [ 1.03543454e-08 -2.47438108e-08]
- XY force grav [ 0.00027648 -0.0002725 ]
- XY pos [-22971.91312552746,22345.880799416333] km
- Velocity at this step [-2491.65216647 -2472.6403546 ]
- Radius 32047.576840511738 km

===== Time 33600(s) =====
- Angle from 

...

- XY force grav [-1.69000651e-04  5.20764527e-05]
- XY pos [45426.286934950076,-13813.873650856378] km
- Velocity at this step [ 923.26726974 2781.20029729]
- Radius 47480.213246553976 km

===== Time 565500(s) =====
- Angle from earth to sail about orbit circle -0.2952087616534226
- Earth angle -16.914216118024573
- Clock angle 36.542891940987715
- XY force sail [9.33439962e-08 6.91791227e-08]
- XY force grav [-1.69158365e-04  5.14400898e-05]
- XY pos [45481.682971134425,-13647.001633018803] km
- Velocity at this step [ 913.12336848 2784.29085343]
- Radius 47484.988569635316 km

===== Time 565560(s) =====
- Angle from earth to sail about orbit circle -0.29150715660029985
- Earth angle -16.70212977105634
- Clock angle 36.64893511447184
- XY force sail [9.29599341e-08 6.91614037e-08]
- XY force grav [-1.69313557e-04  5.08033618e-05]
- XY pos [45536.470373243406,-13479.94418181303] km
- Velocity at this step [ 902.97013264 2787.34320482]
- Radius 47489.77815486265 km

===== Time 565620(s)

- Radius 48263.10631716456 km

===== Time 573900(s) =====
- Angle from earth to sail about orbit circle 0.21554541647523434
- Earth angle 12.34984265742053
- Clock angle 51.17492132871027
- XY force sail [4.43568368e-08 5.51193566e-08]
- XY force grav [-1.67157534e-04 -3.65985917e-05]
- XY pos [47115.01132556774,10493.051334535527] km
- Velocity at this step [-531.38003589 2839.90441135]
- Radius 48269.3320703485 km

===== Time 573960(s) =====
- Angle from earth to sail about orbit circle 0.21913507949300604
- Earth angle 12.555515198213042
- Clock angle 51.27775759910651
- XY force sail [4.40604952e-08 5.49527557e-08]
- XY force grav [-1.66981998e-04 -3.71887988e-05]
- XY pos [47083.12852341422,10663.445599216451] km
- Velocity at this step [-541.39631214 2837.67638059]
- Radius 48275.56383513081 km

===== Time 574020(s) =====
- Angle from earth to sail about orbit circle 0.22272386529283994
- Earth angle 12.761137478120006
- Clock angle 51.38056873906001
- XY force sail [4.37651245e-

- XY force sail [1.25126712e-08 2.77400937e-08]
- XY force grav [-0.00012349 -0.00010903]
- XY pos [36765.03780934396,32688.760555047586] km
- Velocity at this step [-1809.85521539  2188.93474724]
- Radius 49195.76274180253 km

===== Time 582600(s) =====
- Angle from earth to sail about orbit circle 0.7267749252982475
- Earth angle 41.641135875525265
- Clock angle 65.82056793776263
- XY force sail [1.23691050e-08 2.75489522e-08]
- XY force grav [-0.00012308 -0.00010943]
- XY pos [36656.446496420394,32820.096639881696] km
- Velocity at this step [-1817.23908035  2182.37055208]
- Radius 49202.17285035392 km

===== Time 582660(s) =====
- Angle from earth to sail about orbit circle 0.7302362660500339
- Earth angle 41.839456092059265
- Clock angle 65.91972804602963
- XY force sail [1.22265661e-08 2.73580993e-08]
- XY force grav [-0.00012267 -0.00010983]
- XY pos [36547.412151599536,32951.03887300656] km
- Velocity at this step [-1824.59826494  2175.78254157]
- Radius 49208.57951403672 km

=

- XY force sail [1.45619426e-09 7.10621389e-09]
- XY force grav [-6.27752285e-05 -1.46739353e-04]
- XY pos [19503.35658466438,46016.70416900154] km
- Velocity at this step [-2542.58893437  1171.72442673]
- Radius 49979.17546984919 km

===== Time 590400(s) =====
- Angle from earth to sail about orbit circle 1.1699153128216606
- Earth angle 67.0312098124086
- Clock angle 78.51560490620432
- XY force sail [1.42066956e-09 6.99256170e-09]
- XY force grav [-6.22682014e-05 -1.46917142e-04]
- XY pos [19350.80124860231,46087.00763460519] km
- Velocity at this step [-2546.32494121  1162.90981778]
- Radius 49984.65546220225 km

===== Time 590460(s) =====
- Angle from earth to sail about orbit circle 1.1732742474257125
- Earth angle 67.22366258888123
- Clock angle 78.6118312944406
- XY force sail [1.38572276e-09 6.87975080e-09]
- XY force grav [-6.17608216e-05 -1.47093209e-04]
- XY pos [19198.021752129735,46156.78222367221] km
- Velocity at this step [-2550.03050736  1154.08463801]
- Radius 49990.

- XY pos [-3206.692536785192,50523.23865978542] km
- Velocity at this step [-2764.88958991  -119.6698222 ]
- Radius 50624.900214213856 km

===== Time 598800(s) =====
- Angle from earth to sail about orbit circle 1.634180960397981
- Earth angle 93.63167199143984
- Clock angle -88.18416400428008
- XY force sail [ 5.72685728e-12 -1.80641252e-10]
- XY force grav [ 9.85119695e-06 -1.55211131e-04]
- XY pos [-3372.5859121796307,50516.05847045353] km
- Velocity at this step [-2764.29851775  -128.98250088]
- Radius 50628.514684170936 km

===== Time 598860(s) =====
- Angle from earth to sail about orbit circle 1.6374600482182435
- Earth angle 93.81954988419363
- Clock angle -88.09022505790318
- XY force sail [ 6.66208114e-12 -1.99797239e-10]
- XY force grav [ 1.03586148e-05 -1.55155837e-04]
- XY pos [-3538.4438232444354,50508.3195204007] km
- Velocity at this step [-2763.67700046  -138.2918631 ]
- Radius 50632.11357888536 km

===== Time 598920(s) =====
- Angle from earth to sail about orbit circ

In [ ]:

# ORBIT SIM, LONG
init_orbit = 30000E3
# 1.496e+11 m in 1 AU
e = np.array([0,0])
# r = np.array([0, -6.684587e-5])*1.496e+11 # xy pos sail relative to earth, 10000km below in this diagram
r = np.array([0, -init_orbit]) # xy pos sail relative to earth, 10000km below in this diagram
s = np.array([-1, 0])*1.496e+11 # sun is 1 AU to the "left" of earth

mu = 3.986004418*10**14 # SGP earth

m_ss = 0.001
m_earth =  5.972 * 10**24 

n_steps = 10000
t_vec = np.linspace(0,100000, n_steps)
v0 = np.sqrt(np.abs(mu/r[1]))
v0_sail = np.array([v0,0])
clock0 = 0

x,y = r
v = v0_sail
dt = 60 # seconds

# arrays to store and plot
Xs = []
Ys = []
F_sail = []
F_grav = []
Vs = []

for t in range(n_steps): #t_vec:
    print(f"===== Time {t*dt}(s) =====")
    sun2sail = r + np.array([x,y])
    earth_angle = math.atan2(y, x)
    clock_angle = earth2clock(earth_angle) # current hard code "control"

    f_ss = np.array(clock2force(np.deg2rad(clock_angle)))
    f_ge = np.array(grav(x,y,m_ss,m_earth))
    f_gs = np.array([0,0 ]) # no sun gravity yet
    F_sail.append(f_ss)
    F_grav.append(F_grav)
                  
    x = x + v[0]*dt
    y = y + v[1]*dt
    Xs.append(x)
    Ys.append(y)
    f_tot = f_ss + f_ge + f_gs
    
                  
    v = v + (f_tot/m_ss)*dt
    Vs.append(v)
                  
    print(f"- Angle from earth to sail about orbit circle {earth_angle}")
    print(f"- Earth angle {np.rad2deg(earth_angle)}")
    print(f"- Clock angle {clock_angle}")
    print(f"- XY force sail {f_ss}")
    print(f"- XY force grav {f_ge}")
    print(f"- XY pos [{x/1000},{y/1000}] km")
    print(f"- Velocity at this step {v}")
    print(f"- Radius {np.sqrt(x**2+y**2)/1000} km")
    print()

In [16]:
# STATIC PLOT CELL
import plotly.graph_objects as go
Vs = np.stack(Vs)

adjust = 2.5
xm = -adjust*init_orbit
xM = adjust*init_orbit
ym = -adjust*init_orbit
yM = adjust*init_orbit
# Create figure
fig = go.Figure(
    data=[go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="Traj.",
                     mode="lines",
                     line=dict(width=2, color="blue")),
          go.Scatter(x=[0], y=[0],
                     name="Earth",
                     mode="markers",
                     marker=dict(size=20, color="black")),
          go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="curve",
                     showlegend=False,
                     mode="lines",
                     line=dict(width=2, color="blue"))
          ],
    layout=go.Layout(width=1200, height=1200,
                     xaxis=dict(range=[xm, xM], autorange=False, zeroline=True),
                     yaxis=dict(range=[ym, yM], autorange=False, zeroline=True),
                     title=f"Animating Solar Sail Orbit, t:{dt*n_steps}s",
                     hovermode="closest",
                     xaxis_title="X Relative Position to Earth (km)",
                     yaxis_title="Y Relative Position to Earth (km)",
                     plot_bgcolor='white',
                    font=dict(family='Times New Roman', size=30, color='#000000'),

                    ), # was none
)
import os

fig.write_image(os.getcwd() + "/orbit.png")
# fig.show()

In [4]:
# ANIMATION CELL
import plotly.graph_objects as go
Vs = np.stack(Vs)

adjust = 4
xm = -adjust*init_orbit
xM = adjust*init_orbit
ym = -adjust*init_orbit
yM = adjust*init_orbit
# Create figure
fig = go.Figure(
    data=[go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="Traj.",
                     mode="lines",
                     line=dict(width=2, color="blue")),
          go.Scatter(x=[0], y=[0],
                     name="Earth",
                     mode="markers",
                     marker=dict(size=20, color="black")),
          go.Scatter(x=np.stack(Xs).tolist(), y=np.stack(Ys).tolist(),
                     name="curve",
                     showlegend=False,
                     mode="lines",
                     line=dict(width=2, color="blue"))
          ],
    layout=go.Layout(width=600, height=600,
                     xaxis=dict(range=[xm, xM], autorange=False, zeroline=False),
                     yaxis=dict(range=[ym, yM], autorange=False, zeroline=False),
                     title="Animating Solar Sail Orbit + Forces",
                     hovermode="closest",
                     updatemenus=[dict(type="buttons",
                                       buttons=[{
                                            "args": [None, {"frame": {"duration": 50, "redraw": False},
                                                            "fromcurrent": True, "transition": {"duration": 30,
                                                                                                "easing": "quadratic-in-out"}}],
                                            "label": "Play",
                                            "method": "animate"
                                        },
                                        {
                                            "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                                              "mode": "immediate",
                                                              "transition": {"duration": 0}}],
                                            "label": "Pause",
                                            "method": "animate"
                                        },
#                                        {
#                                         "args": [None, {"frame": {"duration": 50, "redraw": True},
#                                                         "fromcurrent": False, "transition": {"duration": 30,
#                                                                                             "easing": "quadratic-in-out"}}],
#                                         "label": "Reset",
#                                         "method": "animate"
#                                     },
                                    ],
                                       direction= "left",
                                    pad= {"r": 10, "t": 70},
                                    x= 0.1,
                                    y= 0,
                                    )]
                    ), # was none

    frames=[go.Frame(
        data=[go.Scatter(
            x=[Xs[k], Xs[k]+1000*Vs[k,0], None, Xs[k], Xs[k]+1000*Vs[k,0]],
            y=[Ys[k], Ys[k]+1000*Vs[k,1], None, Ys[k], Ys[k]+1000*Vs[k,1]],
#             x=[xx[k], xend[k], None, xx[k], xnoe[k]],
#             y=[yy[k], yend[k], None, yy[k], ynoe[k]],
            mode="lines",
            line=dict(color="red", width=4))
        ], 
        name=str(k)) for k in range(n_steps)]
)

def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }
sliders = [
            {
                "pad": {"b": 10, "t": 60},
                "len": 0.7,
                "x": 0.2,
                "y": 0,
                "steps": [
                    {
                        "args": [[f.name], frame_args(0)],
                        "label": str(k),
                        "method": "animate",
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]
                                
fig.update_layout(sliders=sliders)

fig.show()

NameError: name 'Vs' is not defined

In [5]:
import numpy as np
import torch
import torch.optim as optim
import math
import gym
from gym import spaces, logger
from gym.utils import seeding


class RigidEnv(gym.Env):
    """
    Source:
        This file is created by Nathan Lambert, adapted from a model from Somil Bansal
    Observation: 
        Type: Box(12)
        Num	Observation                 Min         Max
        0	x-pos                       -10         10      (meters)
        1	y-pos                       -10         10      (meters)
        2	z-pos                       -10         10      (meters)
        3	x-vel                       -Inf        Inf     (meters/sec)
        4   y-vel                       -Inf        Inf     (meters/sec)
        5   z-vel                       -Inf        Inf     (meters/sec)
        6   roll                        -180        180     (degrees)
        7   pitch                       -90         90      (degrees)
        8   yaw                         -180        180     (degrees)
        9   omega_x                     -Inf        Inf     (rad/s^2)
        10  omega_y                     -Inf        Inf     (rad/s^2)
        11  omega_z                     -Inf        Inf     (rad/s^2)
    """

    def __init__(self, dt=.01, x_noise=0.0, u_noise=0): #0.01 noise
        self.x_dim = 12
        self.u_dim = 4
        self.dt = dt
        self.x_noise = x_noise

        # simulate ten steps per return
        self.dt = self.dt

        # Setup the state indices
        self.idx_xyz = [0, 1, 2]
        self.idx_xyz_dot = [3, 4, 5]
        self.idx_ptp = [6, 7, 8]
        self.idx_ptp_dot = [9, 10, 11]

        self.seed()
        self.viewer = None
        self.state = None
        self.steps_beyond_done = None

    def seed(self, seed=None, inertial=False):
        self.np_random, seed = seeding.np_random(seed)
        if inertial:
            self.Ixx = self.Ixx * self.np_random.uniform(low=0.85, high=1.15, size=1)[0]
            self.Iyy = self.Iyy * self.np_random.uniform(low=0.85, high=1.15, size=1)[0]

        return [seed]

    def step(self, forces, torques):
        # assert self.action_space.contains(u), "%r (%s) invalid" % (u, type(u))

        # We need to convert from upright orientation to N-E-Down that the simulator runs in
        # For reference, a negative thrust of -mg/4 will keep the robot stable
        u = self.pwm_thrust_torque(pwm)
        state = self.state
        self.last_state = state

        dt = self.dt
        u0 = u
        x0 = state
        idx_xyz = self.idx_xyz
        idx_xyz_dot = self.idx_xyz_dot
        idx_ptp = self.idx_ptp
        idx_ptp_dot = self.idx_ptp_dot

        m = self.m
        L = self.L
        Ixx = self.Ixx
        Iyy = self.Iyy
        Izz = self.Izz
        g = self.g
        
        # Cross term, direct term for the three torques
        Tx = np.array([Iyy / Ixx - Izz / Ixx, L / Ixx])
        Ty = np.array([Izz / Iyy - Ixx / Iyy, L / Iyy])
        Tz = np.array([Ixx / Izz - Iyy / Izz, 1. / Izz])

        # # Add noise to input
        # u_noise_vec = np.random.normal(
        #     loc=0, scale=self.u_noise, size=(self.u_dim))
        # u = u+u_noise_vec

        # Array containing the forces
        # This assumes the force all comes directly out of the plane
        # Third column of Qb/i (converts body forces to inertial frame)
        Fxyz = np.zeros(3)
        Fxyz[0] = -1 * (math.cos(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[1]]) * math.cos(x0[idx_ptp[2]]) + math.sin(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[2]])) * u0[0] / m
        Fxyz[1] = -1 * (math.cos(x0[idx_ptp[0]]) * math.sin(x0[idx_ptp[1]]) * math.sin(x0[idx_ptp[2]]) - math.sin(x0[idx_ptp[0]]) * math.cos(x0[idx_ptp[2]])) * u0[0] / m
        Fxyz[2] = g - 1 * (math.cos(x0[idx_ptp[0]]) * math.cos(x0[idx_ptp[1]])) * u0[0] / m

        # Compute the torques
        t0 = np.array([x0[idx_ptp_dot[1]] * x0[idx_ptp_dot[2]], u0[1]])
        t1 = np.array([x0[idx_ptp_dot[0]] * x0[idx_ptp_dot[2]], u0[2]])
        t2 = np.array([x0[idx_ptp_dot[0]] * x0[idx_ptp_dot[1]], u0[3]])
        Txyz = np.array([Tx.dot(t0), Ty.dot(t1), Tz.dot(t2)])

        x1 = np.zeros(12)
        x1[idx_xyz_dot] = x0[idx_xyz_dot] + dt * Fxyz
        x1[idx_ptp_dot] = x0[idx_ptp_dot] + dt * Txyz
        x1[idx_xyz] = x0[idx_xyz] + dt * x0[idx_xyz_dot]
        x1[idx_ptp] = x0[idx_ptp] + dt * self.pqr2rpy(x0[idx_ptp], x0[idx_ptp_dot])

        # makes states less than 1e-12 = 0
        x1[abs(x1) < 1e-15] = 0
        self.state = x1
        state = x1

        # Add noise component
        x_noise_vec = np.random.normal(
            loc=0, scale=self.x_noise, size=(self.x_dim))

        self.state += x_noise_vec

        obs = self.get_obs()
        reward = self.get_reward(obs, u)
        done = self.get_done(obs)

        return obs, reward, done, {}

    def get_obs(self):
        raise NotImplementedError("Subclass must implement this function")

    def set_state(self, x):
        self.state = x

    def reset(self, safe=False):
        x0 = np.array([0, 0, 0])
        v0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))
        # ypr0 = self.np_random.uniform(low=-0.0, high=0.0, size=(3,))
        if safe:
            ypr0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))
            ypr0 = self.np_random.uniform(low=-0.00, high=0.00, size=(3,))
            w0 = self.np_random.uniform(low=-0.00, high=0.00, size=(3,))
        else:
            ypr0 = self.np_random.uniform(low=-np.pi/16., high=np.pi/16., size=(3,))
            w0 = self.np_random.uniform(low=-0.01, high=0.01, size=(3,))

        ypr0[-1] = 0 # 0 out yaw

        self.state = np.concatenate([x0, v0, ypr0, w0])
        self.last_state = self.state
        self.steps_beyond_done = None
        self.interal = 0

        return self.get_obs()

    def get_done(self, state):
        # Done is pitch or roll > 35 deg
        max_a = np.deg2rad(45)
        d = (abs(state[1]) > max_a) or (abs(state[0]) > max_a)
        return d

    def pqr2rpy(self, x0, pqr):
        rotn_matrix = np.array([[1., math.sin(x0[0]) * math.tan(x0[1]), math.cos(x0[0]) * math.tan(x0[1])],
                                [0., math.cos(x0[0]), -math.sin(x0[0])],
                                [0., math.sin(x0[0]) / math.cos(x0[1]), math.cos(x0[0]) / math.cos(x0[1])]])
        return rotn_matrix.dot(pqr)


